In [ ]:
import torch
from transformers import Qwen2_5_VLForConditionalGeneration, AutoProcessor, AutoModel, InternVLChatModel
# from qwen_vl_utils import process_vision_info
from PIL import Image
import os
import numpy as np
from tqdm import tqdm
import math
import torch
from transformers import AutoTokenizer, AutoModel
import timm

# --- Configuration ---
# MODEL_NAME = "OpenGVLab/InternVL3_5-4B"  # You can choose other model sizes
MODEL_NAME = "OpenGVLab/InternVL3_5-4B-Instruct"


IMAGE_DIR = "/home/nguyendc/model-factory/Finetuning-Automation/etc/data/media/docai_mgp_facture_v2_0/"
BATCH_SIZE = 4
# --- End Configuration ---

# Check for GPU availability
device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Using device: {device}")

# Load the model and processor

model = AutoModel.from_pretrained(
    MODEL_NAME,
    torch_dtype=torch.bfloat16,
    use_flash_attn=True,
    attn_implementation="flash_attention_2",
    trust_remote_code=True,
    device_map="cuda").eval()

processor = AutoProcessor.from_pretrained(
    MODEL_NAME, 
    trust_remote_code=True
    )
tokenizer = AutoTokenizer.from_pretrained(
    MODEL_NAME, 
    trust_remote_code=True, 
    use_fast=False
    )

/home/nguyendc/sonnh/venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


2025-09-02 13:50:30.358544: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1756821030.369428 3858431 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1756821030.372761 3858431 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1756821030.382108 3858431 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1756821030.382119 3858431 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1756821030.382121 3858431 computation_placer.cc:177] computation placer alr

[2025-09-02 13:50:35,304] [INFO] [real_accelerator.py:222:get_accelerator] Setting ds_accelerator to cuda (auto detect)


/usr/bin/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status
/usr/bin/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status


Using device: cuda


A new version of the following files was downloaded from https://huggingface.co/OpenGVLab/InternVL3_5-4B-Instruct:
- configuration_intern_vit.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.
A new version of the following files was downloaded from https://huggingface.co/OpenGVLab/InternVL3_5-4B-Instruct:
- configuration_internvl_chat.py
- configuration_intern_vit.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.
A new version of the following files was downloaded from https://huggingface.co/OpenGVLab/InternVL3_5-4B-Instruct:
- conversation.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.
A new version of the following files was downloaded from https://huggingface.co/OpenGVLab/Inte

In [3]:
model

InternVLChatModel(
  (vision_model): InternVisionModel(
    (embeddings): InternVisionEmbeddings(
      (patch_embedding): Conv2d(3, 1024, kernel_size=(14, 14), stride=(14, 14))
    )
    (encoder): InternVisionEncoder(
      (layers): ModuleList(
        (0-23): 24 x InternVisionEncoderLayer(
          (attn): InternAttention(
            (qkv): Linear(in_features=1024, out_features=3072, bias=True)
            (attn_drop): Dropout(p=0.0, inplace=False)
            (proj_drop): Dropout(p=0.0, inplace=False)
            (inner_attn): FlashAttention()
            (proj): Linear(in_features=1024, out_features=1024, bias=True)
          )
          (mlp): InternMLP(
            (act): GELUActivation()
            (fc1): Linear(in_features=1024, out_features=4096, bias=True)
            (fc2): Linear(in_features=4096, out_features=1024, bias=True)
          )
          (norm1): LayerNorm((1024,), eps=1e-06, elementwise_affine=True)
          (norm2): LayerNorm((1024,), eps=1e-06, elementwi

In [9]:
model.vision_model

InternVisionModel(
  (embeddings): InternVisionEmbeddings(
    (patch_embedding): Conv2d(3, 1024, kernel_size=(14, 14), stride=(14, 14))
  )
  (encoder): InternVisionEncoder(
    (layers): ModuleList(
      (0-23): 24 x InternVisionEncoderLayer(
        (attn): InternAttention(
          (qkv): Linear(in_features=1024, out_features=3072, bias=True)
          (attn_drop): Dropout(p=0.0, inplace=False)
          (proj_drop): Dropout(p=0.0, inplace=False)
          (inner_attn): FlashAttention()
          (proj): Linear(in_features=1024, out_features=1024, bias=True)
        )
        (mlp): InternMLP(
          (act): GELUActivation()
          (fc1): Linear(in_features=1024, out_features=4096, bias=True)
          (fc2): Linear(in_features=4096, out_features=1024, bias=True)
        )
        (norm1): LayerNorm((1024,), eps=1e-06, elementwise_affine=True)
        (norm2): LayerNorm((1024,), eps=1e-06, elementwise_affine=True)
        (drop_path1): Identity()
        (drop_path2): Identi

# demo ?

In [4]:
# import math
import numpy as np
import torch
import torchvision.transforms as T
# from decord import VideoReader, cpu
from PIL import Image
from torchvision.transforms.functional import InterpolationMode
# from modelscope import AutoModel, AutoTokenizer

IMAGENET_MEAN = (0.485, 0.456, 0.406)
IMAGENET_STD = (0.229, 0.224, 0.225)

def build_transform(input_size):
    MEAN, STD = IMAGENET_MEAN, IMAGENET_STD
    transform = T.Compose([
        T.Lambda(lambda img: img.convert('RGB') if img.mode != 'RGB' else img),
        T.Resize((input_size, input_size), interpolation=InterpolationMode.BICUBIC),
        T.ToTensor(),
        T.Normalize(mean=MEAN, std=STD)
    ])
    return transform

def find_closest_aspect_ratio(aspect_ratio, target_ratios, width, height, image_size):
    best_ratio_diff = float('inf')
    best_ratio = (1, 1)
    area = width * height
    for ratio in target_ratios:
        target_aspect_ratio = ratio[0] / ratio[1]
        ratio_diff = abs(aspect_ratio - target_aspect_ratio)
        if ratio_diff < best_ratio_diff:
            best_ratio_diff = ratio_diff
            best_ratio = ratio
        elif ratio_diff == best_ratio_diff:
            if area > 0.5 * image_size * image_size * ratio[0] * ratio[1]:
                best_ratio = ratio
    return best_ratio

def dynamic_preprocess(image, min_num=1, max_num=12, image_size=448, use_thumbnail=False):
    orig_width, orig_height = image.size
    aspect_ratio = orig_width / orig_height

    # calculate the existing image aspect ratio
    target_ratios = set(
        (i, j) for n in range(min_num, max_num + 1) for i in range(1, n + 1) for j in range(1, n + 1) if
        i * j <= max_num and i * j >= min_num)
    target_ratios = sorted(target_ratios, key=lambda x: x[0] * x[1])

    # find the closest aspect ratio to the target
    target_aspect_ratio = find_closest_aspect_ratio(
        aspect_ratio, target_ratios, orig_width, orig_height, image_size)

    # calculate the target width and height
    target_width = image_size * target_aspect_ratio[0]
    target_height = image_size * target_aspect_ratio[1]
    blocks = target_aspect_ratio[0] * target_aspect_ratio[1]

    # resize the image
    resized_img = image.resize((target_width, target_height))
    processed_images = []
    for i in range(blocks):
        box = (
            (i % (target_width // image_size)) * image_size,
            (i // (target_width // image_size)) * image_size,
            ((i % (target_width // image_size)) + 1) * image_size,
            ((i // (target_width // image_size)) + 1) * image_size
        )
        # split the image
        split_img = resized_img.crop(box)
        processed_images.append(split_img)
    assert len(processed_images) == blocks
    if use_thumbnail and len(processed_images) != 1:
        thumbnail_img = image.resize((image_size, image_size))
        processed_images.append(thumbnail_img)
    return processed_images

def load_image(image_file, input_size=448, max_num=12):
    image = Image.open(image_file).convert('RGB')
    transform = build_transform(input_size=input_size)
    images = dynamic_preprocess(image, image_size=input_size, use_thumbnail=True, max_num=max_num)
    pixel_values = [transform(image) for image in images]
    pixel_values = torch.stack(pixel_values)
    return pixel_values

# Attention pooling


In [5]:
import torch
import torch.nn.functional as F

def gem_pool(x, p: float = 3.0, eps: float = 1e-6):
    # x: [B, N, D]
    return (x.clamp(min=eps).pow(p).mean(dim=1)).pow(1.0/p)

@torch.no_grad()
def image_embedding(pixel_values, model, use_tiling=True):
    # pixel_values: nếu dùng processor của InternVL, có thể là [T,3,H,W]; nếu bạn tự resize = [1,3,H,W]
    out = model.vision_model(pixel_values=pixel_values, output_hidden_states=True)
    tok = out.last_hidden_state            # [T, N, 1024] hoặc [1, N, 1024]
    if tok.dim() == 2:                     # phòng trường hợp model trả [N, D]
        tok = tok.unsqueeze(0)

    # 1) Attention pooling theo token, trong từng tile
    w_tok = torch.softmax(tok.norm(dim=-1), dim=1).unsqueeze(-1)   # [T,N,1]
    attn_tile = (tok * w_tok).sum(dim=1)                           # [T,1024]

    # 2) Các pooling khác theo token
    mean_tile = tok.mean(dim=1)                                    # [T,1024]
    max_tile  = tok.max(dim=1).values                              # [T,1024]
    gem_tile  = gem_pool(tok, p=3.0)                               # [T,1024]

    # 3) Attention across-tiles (giữ multi-scale nhưng gọn)
    tile_scores = attn_tile.norm(dim=-1)                           # [T]
    w_tile = torch.softmax(tile_scores, dim=0).unsqueeze(-1)       # [T,1]

    mean_vec = (mean_tile * w_tile).sum(dim=0)
    max_vec  = (max_tile  * w_tile).sum(dim=0)
    gem_vec  = (gem_tile  * w_tile).sum(dim=0)
    attn_vec = (attn_tile * w_tile).sum(dim=0)

    # 4) Hợp nhất nhiều “góc nhìn” → 1 vector giàu thông tin
    one_vec = torch.cat([mean_vec, max_vec, gem_vec, attn_vec], dim=0)  # [4*1024]
    one_vec = F.normalize(one_vec, dim=-1).unsqueeze(0)                  # [1, 4096]
    return one_vec.half()  # FP16 để tiết kiệm bộ nhớ

# pool

In [6]:
import torch
import torch.nn.functional as F

# --- Pooling theo token (trong 1 tile) ---
def _pool_tokens(tokens: torch.Tensor, how: str = "mean") -> torch.Tensor:
    """
    tokens: [1, N, D] hoặc [N, D]
    return: [D]
    """
    if tokens.dim() == 3:   # [1, N, D] -> [N, D]
        tokens = tokens.squeeze(0)

    if how == "mean":
        v = tokens.mean(dim=0)
    elif how == "max":
        v = tokens.max(dim=0).values
    elif how == "gem":
        p = 3.0
        v = (tokens.clamp(min=1e-6).pow(p).mean(dim=0)).pow(1.0/p)
    elif how == "cls":
        # chỉ dùng nếu backbone có CLS token ở vị trí đầu
        v = tokens[0]
    else:
        raise ValueError(f"Unknown pooling: {how}")

    return v


@torch.no_grad()
def image_embedding_global(model, pixel_values: torch.Tensor,
                           pool: str = "mean",
                           normalize: bool = False,
                           global_index: int = 0,
                           use_projector: bool = False) -> torch.Tensor:
    """
    Trả về 1 vector [1, D] mô tả toàn ảnh, chỉ dùng GLOBAL tile.
    - pixel_values: [T,3,H,W] (ví dụ T=7) hoặc [1,3,H,W]
    - global_index: thường = 0 (tile toàn ảnh nằm đầu)
    - use_projector: CHỈ bật nếu bạn chắc chắn chiều khớp với projector (mlp1)
    """
    model.eval()
    device = next(model.parameters()).device
    x = pixel_values.to(device)

    out = model.vision_model(pixel_values=x)     # last_hidden_state: [T, N, D] hoặc [1, N, D]
    tok = out.last_hidden_state

    # chọn global tile
    if tok.size(0) > 1:
        tok = tok[global_index:global_index+1]   # [1, N, D]

    # (tuỳ chọn) projector sang không gian khác - cẩn thận mismatch chiều!
    if use_projector:
        # CHỈ nên bật khi biết chắc input dim của mlp1 khớp với tok.size(-1)
        in_feat = getattr(model.mlp1[1], "in_features", None)
        if in_feat is not None and tok.size(-1) == in_feat:
            tok = model.mlp1(tok)                # [1, N, D’]
        else:
            raise ValueError(f"Projector input dim mismatch: tokens={tok.size(-1)} vs mlp1.in={in_feat}")

    v = _pool_tokens(tok, how=pool)              # [D]
    if normalize:
        v = F.normalize(v, dim=-1)
    return v.unsqueeze(0)                        # [1, D]


@torch.no_grad()
def image_embedding_mean(model, pixel_values: torch.Tensor,
                         pool: str = "mean",
                         normalize: bool = True,
                         use_projector: bool = False) -> torch.Tensor:
    """
    Trả về 1 vector [1, D] mô tả toàn ảnh, bằng cách:
      (1) pool theo token trong từng tile → [T, D]
      (2) lấy mean across-tiles → [D]
    """
    model.eval()
    device = next(model.parameters()).device
    x = pixel_values.to(device)

    out = model.vision_model(pixel_values=x)
    tok = out.last_hidden_state                  # [T, N, D] hoặc [1, N, D]

    if use_projector:
        in_feat = getattr(model.mlp1[1], "in_features", None)
        if in_feat is not None and tok.size(-1) == in_feat:
            tok = model.mlp1(tok)
        else:
            raise ValueError(f"Projector input dim mismatch: tokens={tok.size(-1)} vs mlp1.in={in_feat}")

    # pool theo token trong từng tile
    T = tok.size(0)
    per_tile = [ _pool_tokens(tok[t:t+1], how=pool) for t in range(T) ]  # list of [D]
    per_tile = torch.stack(per_tile, dim=0)       # [T, D]

    # mean across-tiles
    v = per_tile.mean(dim=0)                      # [D]
    if normalize:
        v = F.normalize(v, dim=-1)
    return v.unsqueeze(0)                         # [1, D]


# infer

In [7]:
def get_image_embedding(path):
    """
    Processes a batch of images and extracts their embeddings.
    """
    images_pil = []
    valid_paths = []
    if path.lower().endswith(('.png', '.jpg', '.jpeg')):
        try:
            # The processor expects PIL images in RGB format
            # images_pil.append(Image.open(path).convert("RGB"))
            # print(path)
            valid_paths.append(path)
        except Exception as e:
            print(f"Warning: Could not load image {path}. Skipping. Error: {e}")

    if not valid_paths:
        return np.array([]), []

    all_pixel_values = []
    for valid_path in valid_paths:
        pixel_values = load_image(valid_path, max_num=12).to(torch.bfloat16).cuda()
        # print(pixel_values.shape)
        all_pixel_values.append(pixel_values)
    # For pure vision feature extraction, we can provide an empty text prompt.
    # The processor handles tokenizing text and preparing images.
    inputs = torch.cat(all_pixel_values, dim=0).to(device)
   
    # embeddings = image_embedding(inputs, model, use_tiling=True)
    embeddings = image_embedding_mean(model, inputs)
    
    return embeddings.to(torch.float16).cpu().numpy()

In [8]:
import json

# --- Process all images in the directory ---
image_files = [os.path.join(IMAGE_DIR, f) for f in os.listdir(IMAGE_DIR) if f.lower().endswith(('.png', '.jpg', '.jpeg'))]
all_embeddings = []
filepaths = []
BATCH_SIZE = 1

with open("embeddings_factures_osteopathie_1k_InternVL3_5-4B-Instruct.json", "w") as f:

    f.write("[\n")
    first = True
    for i in tqdm(range(0, len(image_files), BATCH_SIZE)):
        batch_paths = image_files[i]
        batch_embeddings = get_image_embedding(batch_paths)
        embeddings_list = [emb.tolist() for emb in batch_embeddings]
        for path, emb in zip(batch_paths, embeddings_list):
            if not first:
                f.write(",\n")
            json.dump({"filepath": path, "embedding": emb}, f)
            first = False
    f.write("\n]\n")

print("Embeddings extracted and saved.")

100%|██████████| 2800/2800 [20:51<00:00,  2.24it/s]

Embeddings extracted and saved.


# check

In [10]:
from sklearn.cluster import DBSCAN, MeanShift, AffinityPropagation
from sklearn.preprocessing import normalize
from sklearn.metrics import silhouette_score
from sklearn.neighbors import NearestNeighbors
from sklearn.decomposition import PCA
import argparse
import warnings
warnings.filterwarnings('ignore')
from sklearn.metrics.pairwise import cosine_similarity
from datetime import datetime


embeddings_path = "/home/nguyendc/sonnh/embedding-clustering/extract/embeddings_factures_osteopathie_1k_InternVL3_5-4B-Instruct.json"
with open(embeddings_path, 'r') as f:
    data = json.load(f)

file_paths = []
embeddings_list = []

for item in data:
    file_paths.append(item['filepath'])
    embeddings_list.append(item['embedding'])

embeddings = np.array(embeddings_list, dtype=np.float32)
print(f"Loaded {len(file_paths)} samples with embedding dimension {embeddings.shape[1]}")

# Normalize embeddings using L2 normalization for cosine distance
embeddings_normalized = normalize(embeddings, norm='l2', axis=1)
print("Applied L2 normalization to embeddings")

sims = cosine_similarity(embeddings)
print(embeddings.shape)
# lấy upper triangle exclude diagonal để inspect
triu_idxs = np.triu_indices_from(sims, k=1)
dist_vals = sims[triu_idxs]
print(dist_vals.shape)
print("mean sim:", dist_vals.mean(), "std:", dist_vals.std())

Loaded 2800 samples with embedding dimension 1024
Applied L2 normalization to embeddings
(2800, 1024)
(3918600,)
mean sim: 0.9939966 std: 0.0073577887


# temp

In [9]:
image_path = "/home/nguyendc/model-factory/Finetuning-Automation/etc/data/media/docai_mgp_facture_v2_0/c363e486-5d45-425e-aef9-4791cad120f7_20250213_120759_1_scale_1.0.jpg"

In [11]:
pixel_values = load_image(image_path, max_num=12).to(torch.bfloat16).cuda()
generation_config = dict(max_new_tokens=1024, do_sample=True)



question = '<image>\nPlease describe the image shortly.'
response = model.chat(tokenizer, pixel_values, question, generation_config)
print(f'User: {question}\nAssistant: {response}')

# single-image multi-round conversation (单图多轮对话)
question = '<image>\nPlease describe the image in detail.'
response, history = model.chat(tokenizer, pixel_values, question, generation_config, history=None, return_history=True)
print(f'User: {question}\nAssistant: {response}')

Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


User: <image>
Please describe the image shortly.
Assistant: The image shows a receipt for a consultation with Noël Breignaud, an osteopath. It includes his contact information, with the address "104, cours des fossés, 33210 Langon" and his phone number. The receipt details a payment of 55€ for a consultation dated 15/06/2020. The receipt number is 1750401922774. There are handwritten details and signatures, with the amount and date written in ink. Noël Breignaud's signature and a circular stamp are also present.
User: <image>
Please describe the image in detail.
Assistant: The image is a handwritten receipt or invoice from a practitioner named Noël Breign aud, who is an osteopath. The text on the left side of the document includes the following details:

- **Name:** Noël Breignaud
- **Profession:** Ouestopathe (Osteopath)
- **Address:** 104, cours des fossés, 33210 Lagnon
- **Phone Number:** Tel. 06 88 70 66 43

On the right side, there are registration and identification numbers:

- *

In [23]:
vout = model.vision_model(pixel_values=pixel_values, output_hidden_states=True)

In [ ]:
patch_feats = vout.last_hidden_state             # [B, N_patches, Dv], Dv ~ 1024 theo kiến trúc của bạn
print(patch_feats.shape)
# Nếu backbone có CLS token, bạn có thể dùng patch_feats[:,0]
# Cách an toàn chung: mean-pool
# img_vec = patch_feats.mean(dim=1)                # [B, Dv]
# img_vec = torch.nn.functional.normalize(img_vec, dim=-1)  # L2 normalize cho retrieval

torch.Size([7, 1025, 1024])


In [ ]:
# img_vec.shape

torch.Size([7, 1024])